In [3]:
import requests
from datetime import datetime
import time
import pandas as pd
from tqdm import tqdm
import pymysql

In [4]:
db = pymysql.connect(
    host='localhost',
    port=3306,
    user='root',
    passwd='yourPasswd',
    db='coin_db',
    charset='utf8'
)

In [5]:
cursor = db.cursor()

In [6]:
url = 'https://api.binance.com/api/v3/klines'
coin_name = "BTCUSDT"
start_date = "2023-09-15"
end_date = "2023-09-26"

In [7]:
# 문자열 형태의 start_date 0시 0분을 datetime으로 변환합니다.
datetime.strptime(start_date + ' 00:00', '%Y-%m-%d %H:%M').timetuple()

time.struct_time(tm_year=2023, tm_mon=9, tm_mday=15, tm_hour=0, tm_min=0, tm_sec=0, tm_wday=4, tm_yday=258, tm_isdst=-1)

In [8]:
# 변환 결과를 정수로 변환합니다.
# 변환 결과는 1/1000초 단위이기 때문에, 결과를 1000으로 나눠서 1초 단위로 변환합니다.
int(time.mktime(datetime.strptime(start_date + ' 00:00', '%Y-%m-%d %H:%M').timetuple())) * 1000

1694703600000

In [9]:
start = int(time.mktime(datetime.strptime(start_date + ' 00:00', '%Y-%m-%d %H:%M').timetuple())) * 1000
end = int(time.mktime(datetime.strptime(end_date + ' 23:59', '%Y-%m-%d %H:%M').timetuple())) * 1000

In [10]:
# 바이낸스 API 파라미터 정보
params = {
    'symbol': coin_name, # 코인 이름 - BTCUSDT(비트코인), ETHUSDT(이더리움)
    'interval': '1m', # 수집 시간 간격 - 1m (1분), 1h(1시간)
    'limit' : 1000, # 한번에 가져올 데이터의 수
    'startTime': start,
    'endTime': end
}

In [11]:
# start가 end보다 작을 동안 반복
while start < end:
    # 시작 시간 갱신
    params['startTime'] = start
    # 바이낸스 API 접속 결과 리턴
    ## 접속 결과(비트코인 가격)을 result에 저장
    result = requests.get(url, params=params)
    coin_list = result.json()
    
    if not coin_list:
        break
    
    # coin_list에서 코인 가격 하나를 coin 변수에 저장
    for coin in coin_list:
        print('coin =', coin)
        open_time = datetime.fromtimestamp(coin[0] // 1000)
        print("open_time =", open_time)
        open_price = coin[1]
        print("open_price =", open_price)
        high_price = coin[2]
        print("high_price =", high_price)
        low_price = coin[3]
        print("low_price =", low_price)
        close_price = coin[4]
        print("close_price =", close_price)
        volume = coin[5]
        print("volume =", volume)
        print("=" * 50)
        
        sql = "INSERT INTO coin_tbl (open_time,open_price,high_price,low_price,close_price,volume,symbol) "
        sql += " VALUES (%s, %s, %s, %s, %s, %s, %s)"
        
        cursor.execute(sql, (open_time, open_price, high_price, low_price, close_price, volume, coin_name))
        db.commit()
    
    # coin_list[-1][0]: 코인 리스트 마지막 행 0번째 열 -> 수집한 마지막 시간이 int로 저장되어 있음
    start = coin_list[-1][0] + 60000 # 다음 step으로
    time.sleep(1)

db.close()

coin = [1694703600000, '26731.39000000', '26798.50000000', '26699.62000000', '26699.99000000', '237.93550000', 1694703659999, '6367147.16550550', 4170, '144.37313000', '3863681.93116030', '0']
open_time = 2023-09-15 00:00:00
open_price = 26731.39000000
high_price = 26798.50000000
low_price = 26699.62000000
close_price = 26699.99000000
volume = 237.93550000
coin = [1694703660000, '26699.99000000', '26717.33000000', '26666.11000000', '26677.36000000', '171.17584000', 1694703719999, '4570113.63198620', 2337, '73.14697000', '1952983.12046470', '0']
open_time = 2023-09-15 00:01:00
open_price = 26699.99000000
high_price = 26717.33000000
low_price = 26666.11000000
close_price = 26677.36000000
volume = 171.17584000
coin = [1694703720000, '26677.36000000', '26707.65000000', '26677.36000000', '26696.84000000', '50.07833000', 1694703779999, '1336862.77371240', 911, '21.35753000', '570110.24331110', '0']
open_time = 2023-09-15 00:02:00
open_price = 26677.36000000
high_price = 26707.65000000
low_pr